<a href="https://colab.research.google.com/github/nicovaras/deep-learning-projects/blob/main/Music_generation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import os

inputs_raw = []

folder_path = "/content/drive/MyDrive/music_gen/midi_0"
files = os.listdir(folder_path)

In [ ]:
!sudo apt install -y fluidsynth
!pip install --upgrade pyfluidsynth
!pip install --upgrade pretty_midi

Reading package lists... Done
Building dependency tree       
Reading state information... Done
fluidsynth is already the newest version (2.1.1-2).
0 upgraded, 0 newly installed, 0 to remove and 23 not upgraded.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import numpy as np
import pretty_midi

def midi_to_piano_roll(midi_file, fs=16):
    midi_data = pretty_midi.PrettyMIDI(midi_file)
    midi_data.instruments[0].program = 0
    midi_data.instruments[0].is_drum = False
    piano_roll = midi_data.get_piano_roll(fs=fs)
    return piano_roll

def binarize_piano_roll(piano_roll, threshold=0):
    return (piano_roll > threshold).astype(np.float32)

def split_piano_roll(piano_roll, sequence_length):
    num_sequences = piano_roll.shape[1] // sequence_length
    return np.array_split(piano_roll[:, :num_sequences * sequence_length], num_sequences, axis=1)


In [ ]:
sequences = []
sequence_length = 256
fs = 48

for i, file in enumerate(files):
  print(i,len(files), file)
  midi_file = os.path.join(folder_path, file)
  piano_roll = midi_to_piano_roll(midi_file, fs=fs)
  piano_roll = binarize_piano_roll(piano_roll)
  if piano_roll.size == 0:
    continue
  try:
    sequences += split_piano_roll(piano_roll, sequence_length)
  except:
    print('err')
    continue
input_data = np.array(sequences).transpose(0, 2, 1)
input_data.shape


0 110 7.mid
1 110 9.mid
2 110 4.mid
3 110 8.mid
4 110 6.mid
5 110 5.mid
6 110 1.mid
7 110 17.mid
8 110 23.mid
9 110 14.mid
10 110 21.mid
11 110 20.mid
12 110 11.mid
13 110 12.mid
14 110 13.mid
15 110 10.mid
16 110 31.mid
17 110 35.mid
18 110 34.mid
19 110 33.mid
20 110 29.mid
21 110 41.mid
22 110 37.mid
23 110 38.mid
24 110 40.mid
25 110 36.mid
26 110 39.mid
27 110 53.mid
28 110 48.mid
29 110 51.mid
30 110 50.mid
31 110 54.mid
32 110 66.mid
33 110 57.mid
34 110 65.mid
35 110 68.mid
36 110 62.mid
37 110 59.mid
38 110 64.mid
39 110 60.mid
40 110 67.mid
41 110 70.mid
42 110 78.mid
43 110 69.mid
44 110 84.mid
45 110 83.mid
46 110 79.mid
47 110 85.mid
48 110 80.mid
49 110 82.mid
50 110 88.mid
51 110 90.mid
52 110 91.mid
53 110 87.mid
54 110 92.mid
55 110 96.mid
56 110 101.mid
57 110 97.mid
58 110 104.mid
59 110 100.mid
60 110 99.mid
61 110 102.mid
62 110 98.mid
63 110 93.mid
64 110 95.mid
65 110 111.mid
66 110 110.mid
67 110 106.mid
68 110 112.mid
69 110 117.mid
70 110 120.mid
71 110 118.mi

(4847, 256, 128)

In [ ]:
idx=600

generated_sequence = input_data[idx]
generated_sequence_int = (generated_sequence * 127).astype(np.int32)
print("Unique velocities:", np.unique(generated_sequence_int))

midi_data = piano_roll_to_midi(generated_sequence_int.T, program=9, fs=fs)
midi_data.write('output_midi_file.mid')
print(input_data[idx].argmax(axis=1))
_SAMPLING_RATE = 48000
def display_audio(pm: pretty_midi.PrettyMIDI, seconds=30):
  waveform = pm.fluidsynth(fs=_SAMPLING_RATE)
  # Take a sample of the generated waveform to mitigate kernel resets
  waveform_short = waveform[:seconds*_SAMPLING_RATE]
  return display.Audio(waveform_short, rate=_SAMPLING_RATE)
pm = pretty_midi.PrettyMIDI("output_midi_file.mid")  
display_audio(pm)

Unique velocities: [  0 127]
[40 40 40 40 40 40 40 40 44 44 44 44 44 44 44 44 44 44 35 35 35 35 35 35
 35 35 35 44 44 44 44 44 44 44 44 44 40 40 40 40 40 40 40 40 40 40 35 35
 35 35 35 35 35 35 35 44 44 44 44 44 44 44 44 44 44 35 35 35 35 35 35 35
 35 35 40 40 40 40 40 40 40 40 40 44 44 44 44 44 44 44 44 44 44 35 35 35
 35 35 35 35  0  0 44 44 44 44 44 44 44 44 44 40 40 40 40 40 40 40 40 40
 40 44 44 44 44 44 44 44 44 44 35 35 35 35 35 35 35 35 35 44 44 44 44 44
 44 44 44 44 44 40 40 40 40 40 40 40 40 40 44 44 44 44 44 44 44 44 44 35
 35 35 35 35 35 35 35 35 35 44 44 44 44 44 44 44 44 44 40 40 40 40 40 40
 40 40 40 35 35 35 35 35 35 35 35 35 35 44 44 44 44 44 44 44 44 44 35 35
 35 35 35 35 35 35 35 40 40 40 40 40 40 40 40 40 40 44 44 44 44 44 44 44
 44 44 35 35 35 35 35 35 35  0  0  0 44 44 44 44]


In [ ]:
import tensorflow as tf
from keras import backend as K

# Print TensorFlow device list
sess = tf.compat.v1.Session(config=tf.compat.v1.ConfigProto(log_device_placement=True))
K.set_session(sess)

Device mapping:
/job:localhost/replica:0/task:0/device:GPU:0 -> device: 0, name: Tesla T4, pci bus id: 0000:00:04.0, compute capability: 7.5



In [ ]:
import numpy as np
from sklearn.metrics import f1_score
from keras.models import Sequential
from keras.layers import LSTM, Dense, TimeDistributed, Dropout, GRU
from keras.callbacks import LambdaCallback
from keras.callbacks import EarlyStopping


In [ ]:
train_ratio = 0.8
num_train = int(train_ratio * input_data.shape[0])
X_train, X_val = input_data[:num_train], input_data[num_train:]
X_train.shape, X_val.shape

((3877, 256, 128), (970, 256, 128))

In [ ]:
X = X_train
Y = X_train
X_val2 = X_val

In [ ]:

# Build the model

input_shape = (sequence_length, 128)

model = Sequential()
model.add(GRU(units=2048, input_shape=input_shape, return_sequences=True))
model.add(Dropout(0.5))
# model.add(GRU(units=512, input_shape=(seq_length, num_drums), return_sequences=True))
# model.add(Dropout(0.3))
# model.add(LSTM(units=256, return_sequences=True))
# model.add(Dropout(0.3))
model.add(TimeDistributed(Dense(2048, activation="sigmoid")))
model.add(Dropout(0.3))
model.add(TimeDistributed(Dense(128, activation="sigmoid")))
model.compile(loss="binary_crossentropy", optimizer="adam")

# Custom callback to compute F1-score on validation set
def on_epoch_end(epoch, logs):
    y_pred = np.argmax(model.predict(X_val) > 0.5, axis=2)
    y_true = np.argmax(X_val > 0.5, axis=2)
    f1 = f1_score(y_true.ravel(), y_pred.ravel(), average='macro')
    print(f"\nEpoch {epoch + 1} - F1-score on validation set: {f1:.4f}")

f1_callback = LambdaCallback(on_epoch_end=on_epoch_end)
early_stopping = EarlyStopping(monitor='val_loss', patience=20, restore_best_weights=True)

# Train the model
model.fit(X_train, X_train, validation_split=0.2, epochs=1000, batch_size=32, callbacks=[f1_callback, early_stopping], verbose=1)

# Epoch 50 - F1-score on validation set: 0.6964
# 172/172 [==============================] - 17s 100ms/step - loss: 1.9648e-06 - val_loss: 7.5823e-07

Epoch 1/1000
31/31 [==============================] - 4s 106ms/step

Epoch 1 - F1-score on validation set: 0.0101
97/97 [==============================] - 43s 413ms/step - loss: 0.0476 - val_loss: 0.0357
Epoch 2/1000
31/31 [==============================] - 3s 106ms/step

Epoch 2 - F1-score on validation set: 0.1507
97/97 [==============================] - 36s 369ms/step - loss: 0.0266 - val_loss: 0.0228
Epoch 3/1000
31/31 [==============================] - 3s 109ms/step

Epoch 3 - F1-score on validation set: 0.4493
97/97 [==============================] - 37s 378ms/step - loss: 0.0093 - val_loss: 0.0059
Epoch 4/1000
31/31 [==============================] - 3s 108ms/step

Epoch 4 - F1-score on validation set: 0.6648
97/97 [==============================] - 38s 394ms/step - loss: 0.0022 - val_loss: 0.0031
Epoch 5/1000
31/31 [==============================] - 3s 109ms/step

Epoch 5 - F1-score on validation set: 0.6766
97/97 [==============================] - 37s 377ms/step - loss: 9.2106

In [ ]:
model.save('/content/drive/MyDrive/music_gen/model_0.h5')

In [ ]:
import keras
model = keras.models.load_model('/content/drive/MyDrive/music_gen/model_0.h5')


In [ ]:
import tensorflow as tf

def generate_sequence(model, seed_sequence, output_length):
    generated_sequence = seed_sequence
    
    for _ in range(output_length):
        input_sequence = np.array([generated_sequence[-seed_sequence.shape[0]:]])
        # input_sequence = tf.convert_to_tensor(input_sequence, dtype=tf.float32)
        next_step_probs = model.predict(input_sequence)[0]


        # Sample from the output probabilities
        next_step = (next_step_probs > 0.5).astype(np.float32)

        # Append the next time step to the generated sequence
        generated_sequence = np.vstack([generated_sequence, next_step])

    return np.array(generated_sequence)

# Choose a random seed sequence from the input data
seed_idx = np.random.randint(len(input_data))
seed_sequence = input_data[seed_idx]

# Generate a new sequence of desired length
output_length = 8
generated_sequence = generate_sequence(model, seed_sequence, output_length)


1/1 [==============================] - 0s 33ms/step


In [ ]:
generated_sequence.argmax(axis=1)

array([42, 42, 42, ..., 38, 38, 38])

In [ ]:
def piano_roll_to_midi(piano_roll, fs=48, program=0):
    notes, frames = piano_roll.shape
    pm = pretty_midi.PrettyMIDI()
    instrument = pretty_midi.Instrument(program=program, is_drum=True)

    # pad 1 column of zeros so we can acknowledge inital and ending events
    piano_roll = np.pad(piano_roll, [(0, 0), (1, 1)], 'constant')

    # use changes in velocities to find note on / note off events
    velocity_changes = np.nonzero(np.diff(piano_roll).T)

    # keep track on velocities and note on times
    prev_velocities = np.zeros(notes, dtype=int)
    note_on_time = np.zeros(notes)

    for time, note in zip(*velocity_changes):
        # use time + 1 because of padding above
        velocity = piano_roll[note, time + 1]
        time = time / fs
        if velocity > 0:
            if prev_velocities[note] == 0:
                note_on_time[note] = time
                prev_velocities[note] = velocity
        else:
            pm_note = pretty_midi.Note(
                velocity=prev_velocities[note],
                pitch=note,
                start=note_on_time[note],
                end=time)
            instrument.notes.append(pm_note)
            prev_velocities[note] = 0
    pm.instruments.append(instrument)
    return pm


In [ ]:
# generated_sequence = input_data[0]
generated_sequence_int = (generated_sequence * 127).astype(np.int32)
print("Unique velocities:", np.unique(generated_sequence_int))

midi_data = piano_roll_to_midi(generated_sequence_int.T, program=9, fs=48)
midi_data.write('output_midi_file.mid')

generated_sequence_int = (seed_sequence * 127).astype(np.int32)
midi_data = piano_roll_to_midi(generated_sequence_int.T, program=9, fs=48)
midi_data.write('output_midi_file_seed.mid')


Unique velocities: [  0 127]


In [ ]:
import fluidsynth
import pretty_midi
from IPython import display

_SAMPLING_RATE = 48000
def display_audio(pm: pretty_midi.PrettyMIDI, seconds=30):
  waveform = pm.fluidsynth(fs=_SAMPLING_RATE)
  # Take a sample of the generated waveform to mitigate kernel resets
  waveform_short = waveform[:seconds*_SAMPLING_RATE]
  return display.Audio(waveform_short, rate=_SAMPLING_RATE)
pm = pretty_midi.PrettyMIDI("output_midi_file_seed.mid")  
display_audio(pm)

In [ ]:
import fluidsynth
import pretty_midi
from IPython import display

_SAMPLING_RATE = 48000
def display_audio(pm: pretty_midi.PrettyMIDI, seconds=30):
  waveform = pm.fluidsynth(fs=_SAMPLING_RATE)
  # Take a sample of the generated waveform to mitigate kernel resets
  waveform_short = waveform[:seconds*_SAMPLING_RATE]
  return display.Audio(waveform_short, rate=_SAMPLING_RATE)
pm = pretty_midi.PrettyMIDI("output_midi_file.mid")  
display_audio(pm)

In [ ]:
generated_sequence_int.max()

127

In [ ]:

# Post-process the output
def post_process_pattern(pattern, resolution=96):
    events = []
    for i, row in enumerate(pattern):
        for j, value in enumerate(row):
            if value:
                events.append((i * resolution, "note_on", j, 127))
                events.append(((i + 1) * resolution, "note_off", j, 0))

    return events

res2 = post_process_pattern(res)

# Save the generated sequence as a MIDI file
def events_to_midi(events, output_file):
    midi = MidiFile()
    track = MidiTrack()
    midi.tracks.append(track)

    for event in events:
        ms_since_start, event_type, midi_sound, volume = event
        message = Message(event_type, channel=0, note=midi_sound, velocity=volume, time=ms_since_start)
        track.append(message)

    midi.save(output_file)

events_to_midi(res2, "generated_guitar_pattern1.mid")

In [ ]:
res2

[(0, 'note_on', 75, 127),
 (96, 'note_off', 75, 0),
 (192, 'note_on', 77, 127),
 (288, 'note_off', 77, 0),
 (480, 'note_on', 82, 127),
 (576, 'note_off', 82, 0),
 (672, 'note_on', 82, 127),
 (768, 'note_off', 82, 0),
 (1152, 'note_on', 77, 127),
 (1248, 'note_off', 77, 0),
 (1440, 'note_on', 63, 127),
 (1536, 'note_off', 63, 0),
 (1632, 'note_on', 82, 127),
 (1728, 'note_off', 82, 0),
 (2880, 'note_on', 77, 127),
 (2976, 'note_off', 77, 0),
 (3072, 'note_on', 75, 127),
 (3168, 'note_off', 75, 0),
 (3360, 'note_on', 77, 127),
 (3456, 'note_off', 77, 0),
 (3552, 'note_on', 77, 127),
 (3648, 'note_off', 77, 0),
 (3840, 'note_on', 77, 127),
 (3936, 'note_off', 77, 0),
 (3936, 'note_on', 75, 127),
 (4032, 'note_off', 75, 0),
 (4128, 'note_on', 72, 127),
 (4224, 'note_off', 72, 0),
 (4320, 'note_on', 75, 127),
 (4416, 'note_off', 75, 0),
 (5280, 'note_on', 72, 127),
 (5376, 'note_off', 72, 0),
 (5472, 'note_on', 75, 127),
 (5568, 'note_off', 75, 0),
 (5760, 'note_on', 72, 127),
 (5856, 'note

In [ ]:
!sudo apt install -y fluidsynth

Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following additional packages will be installed:
  fluid-soundfont-gm libfluidsynth2 libinstpatch-1.0-2 qsynth
  timgm6mb-soundfont
Suggested packages:
  fluid-soundfont-gs timidity jackd musescore
The following NEW packages will be installed:
  fluid-soundfont-gm fluidsynth libfluidsynth2 libinstpatch-1.0-2 qsynth
  timgm6mb-soundfont
0 upgraded, 6 newly installed, 0 to remove and 23 not upgraded.
Need to get 126 MB of archives.
After this operation, 157 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu focal/universe amd64 fluid-soundfont-gm all 3.1-5.1 [119 MB]
Get:2 http://archive.ubuntu.com/ubuntu focal/universe amd64 libinstpatch-1.0-2 amd64 1.1.2-2build1 [238 kB]
Get:3 http://archive.ubuntu.com/ubuntu focal/universe amd64 timgm6mb-soundfont all 1.3-3 [5,420 kB]
Get:4 http://archive.ubuntu.com/ubuntu focal/universe amd64 libfluidsynth2 amd64 2.1.1-2 [

In [ ]:
!pip install --upgrade pyfluidsynth

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
!pip install pretty_midi

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import pretty_midi

# Create a new PrettyMIDI object
midi = pretty_midi.PrettyMIDI()

# Create a new drum track
drum_track = pretty_midi.Instrument(program=0, is_drum=False)

# Keep track of active notes
active_notes = {}

# Add notes to the drum track
for event in res2:
    if event[1] == 'note_on':
        note = pretty_midi.Note(
            velocity=event[3],
            pitch=event[2],
            start=midi.tick_to_time(event[0]),
            end=(midi.tick_to_time(event[0])+96)
        )
        drum_track.notes.append(note)
        active_notes[event[2]] = note
    elif event[1] == 'note_off':
        if event[2] in active_notes:
            active_notes[event[2]].end = midi.tick_to_time(event[0])
            del active_notes[event[2]]

# Add the drum track to the MIDI object
midi.instruments.append(drum_track)

# Save the MIDI file
midi.write('generated_guitar_pattern3.mid')



In [ ]:
import fluidsynth
import pretty_midi
from IPython import display

_SAMPLING_RATE = 16000
def display_audio(pm: pretty_midi.PrettyMIDI, seconds=30):
  waveform = pm.fluidsynth(fs=_SAMPLING_RATE)
  # Take a sample of the generated waveform to mitigate kernel resets
  waveform_short = waveform[:seconds*_SAMPLING_RATE]
  return display.Audio(waveform_short, rate=_SAMPLING_RATE)
pm = pretty_midi.PrettyMIDI("generated_guitar_pattern3.mid")  
display_audio(pm)

In [ ]:
res

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [ ]:
idx = np.argmax(y_true, axis=2)

y_true.shape, idx.shape, idx[0].shape, idx[0], y_true[0][0]
# idx = np.argmax(idx, axis=1)

# # Set elements without a True value to -1
# idx[np.sum(y_pred, axis=1) == 0] = -1

# # Print the result
# print(idx)


NameError: ignored

In [ ]:
arr = np.zeros((3, 4, 5), dtype=bool)
arr[0, 2, 3] = True
arr[1, 1, 2] = True
arr[2, 0, 0] = True

# Find the index of the first True value for each element
idx = np.argmax(arr, axis=1)

# Set elements without a True value to -1
idx[np.sum(arr, axis=1) == 0] = -1

# Print the result
print(idx)

[[-1 -1 -1  2 -1]
 [-1 -1  1 -1 -1]
 [ 0 -1 -1 -1 -1]]


In [ ]:
import os

inputs_raw = []

folder_path = "/content/drive/MyDrive/music_gen/inputs_0"
files = os.listdir(folder_path)
for i, file in enumerate(files):
    file_path = os.path.join(folder_path, file)
    
    with open(file_path, "r") as file_in:
        inputs_raw.append([x.strip() for x in file_in.readlines()])

inputs_raw2 = []

for input in inputs_raw:
  new_input = []
  for line in input:
    if "off" in line:
      continue
    new_input.append(f'{line.split(" ")[2]} {line.split(" ")[-1]} ')
  inputs_raw2.append(new_input)
inputs_raw = inputs_raw2


inputs_raw2 = []
for input in inputs_raw:
  input_2 = []
  for i in range(0,len(input), 10):
    s = ''
    for j in range(min(10,len(input)-i)):
      s += input[i+j]
    l = [int(x) for x in [y for y in s.split(" ") if y != '']]
    val = l[1]
    for j in range(1,len(l),2):
      l[j] -= val
      l[j] = l[j]//480
    input_2.append(' '.join([str(x) for x in l]))
  inputs_raw2.append(list(set(input_2)))
len(inputs_raw2[0])

138

In [ ]:
len(list(set(inputs_raw2[0])))

138

In [ ]:
train_data = inputs_raw2[:50]
valid_data = inputs_raw2[50:52]

In [ ]:
import torch
from transformers import GPT2LMHeadModel, GPT2Tokenizer

model = GPT2LMHeadModel.from_pretrained('gpt2').to('cuda')
tokenizer = GPT2Tokenizer.from_pretrained('gpt2')
tokenizer.add_special_tokens({'pad_token': '[PAD]'})

optimizer = torch.optim.Adam(model.parameters(), lr=0.001)
num_epochs = 5
for epoch in range(num_epochs):
    print(f"epoch {epoch}")
    for inputs in train_data:
        cuda_inputs = []
        for input in inputs:
          cuda_inputs.append(tokenizer(input, return_tensors="pt", padding=True).to('cuda'))
        for i, input in enumerate(cuda_inputs):
          if i % 20 == 0:
            optimizer.zero_grad()
          outputs = model(**input, labels=input["input_ids"])
          loss = outputs.loss
          loss.backward()
          optimizer.step()
        print(loss.item())

    print("val")
    with torch.no_grad():
        val_loss = 0
        for inputs in valid_data:
            cuda_inputs = []
            for input in inputs:
              cuda_inputs.append(tokenizer(input, return_tensors="pt", padding=True).to('cuda'))        

            mean_loss = 0
            for i, input in enumerate(cuda_inputs):
              outputs = model(**input, labels=input["input_ids"])
              mean_loss += outputs.loss
            
            val_loss += mean_loss/len(cuda_inputs)
    # Print the average validation loss for this epoch
    print("Epoch: {}/{} Validation Loss: {:.4f}".format(epoch + 1, num_epochs, val_loss / len(valid_data)))



epoch 0
4.6678338050842285
2.228943109512329
6.279392242431641
1.9469472169876099
2.508208751678467
1.5069411993026733
1.4008499383926392
5.466958999633789
2.3328723907470703
1.2062777280807495
4.168835163116455
3.8773298263549805
2.6659202575683594
2.0891871452331543
1.4189627170562744
2.6224446296691895
2.593716621398926
1.4481804370880127
1.5210316181182861
1.7956088781356812
2.080904722213745
2.3083064556121826
3.275175094604492
2.0093793869018555
1.1171505451202393
2.519817352294922
1.3091657161712646
2.4407737255096436
1.499875545501709
9.816566467285156
2.4480814933776855
1.1323823928833008
1.7995179891586304
1.8486195802688599
3.1467392444610596
2.211668014526367
1.9454803466796875
1.1858433485031128
1.562868595123291
1.4083689451217651
1.7649474143981934
1.5807403326034546
1.2581697702407837
1.3201713562011719
1.8602204322814941
2.1192774772644043
1.4276944398880005
1.653845191001892
0.865683376789093
1.0371525287628174
val
Epoch: 1/5 Validation Loss: 2.8714
epoch 1
1.75259315

In [ ]:
inputs = tokenizer(" 35", return_tensors="pt").to('cuda')
res = model.generate(**inputs, return_dict_in_generate=True, output_scores=True, max_length=100)

tokenizer.decode(res.sequences[0])

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


' 35 0 36 1 36 1 36 1 36 1 36 1 36 1 36 1 36 1 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36 36'

In [ ]:
train_data[0]

['35 0 40 0 46 0 35 2 46 2 35 3 35 3 35 4 40 4 46 4',
 '41 0 44 0 41 1 41 2 44 2 48 3 44 4 41 5 41 6 44 6',
 '35 0 46 0 35 0 40 1 46 1 35 1 35 2 46 2 35 2 41 3',
 '35 0 59 0 59 1 40 2 59 2 59 3 35 4 59 4 35 5 59 5',
 '35 0 35 0 40 1 46 1 35 3 46 3 35 3 35 4 35 4 40 5',
 '46 0 35 1 46 1 35 1 35 2 46 2 35 2 40 3 46 3 35 4',
 '59 0 40 1 59 1 59 2 35 3 57 3 59 4 40 5 59 5 59 6',
 '59 0 40 1 59 1 59 2 35 3 59 3 35 4 59 4 40 5 59 5',
 '52 0 49 0 44 2 48 3 44 4 41 5 41 6 44 6 50 7 44 8',
 '35 0 40 0 40 1 35 2 49 2 46 3 40 4 46 4 46 5 35 6',
 '35 0 46 0 35 1 46 1 35 1 35 2 46 2 35 2 40 3 46 3',
 '35 0 40 0 46 0 35 1 35 1 46 1 35 2 41 2 49 2 35 3',
 '59 0 40 1 59 1 35 1 59 2 40 2 35 3 49 3 59 4 40 5',
 '41 0 41 1 44 1 48 2 44 3 41 4 41 5 44 5 41 6 41 7',
 '35 0 35 0 35 0 40 1 35 2 57 2 40 3 35 4 49 4 40 5',
 '41 0 35 0 35 0 35 1 40 1 35 2 49 2 40 3 35 4 57 4',
 '40 0 46 0 35 1 46 1 35 2 46 2 35 2 35 3 46 3 35 3',
 '40 0 46 0 46 1 35 2 46 2 46 3 40 4 46 4 46 5 35 6',
 '48 0 44 1 41 2 47 3 44 3 4

In [ ]:

with torch.no_grad():
    for inputs in valid_data:
        # Tokenize the inputs and convert them to tensors
        cuda_inputs = []
        for input in inputs:
          cuda_inputs.append(tokenizer(input, return_tensors="pt", padding=True).to('cuda'))        

        outputs = model(inputs_ids=tokens, labels=tokens)
        loss = outputs[0]

        # Accumulate the validation loss
        val_loss += loss.mean().item()
# Print the average validation loss for this epoch
print("Epoch: {}/{} Validation Loss: {:.4f}".format(epoch + 1, num_epochs, val_loss / len(valid_data)))

In [ ]:
len(inputs_raw)

110